<a href="https://colab.research.google.com/github/LES4975/Album_Art_Generator_Project/blob/main/music_classification.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Google Colab용 음악 장르 및 분위기 분류기
# Essentia 네이티브 라이브러리 사용

# =============================================================================
# 1. 환경 설정 및 라이브러리 설치
# =============================================================================
# 1단계: numpy를 먼저 호환 버전으로 고정
!pip install "numpy==1.26.4" --force-reinstall

# 2단계: Essentia 최신 버전 설치 (numpy 버전 고정 상태에서)
!pip install essentia-tensorflow --no-deps --force-reinstall

# 3단계: Essentia 의존성들 개별 설치 (numpy 제외)
!pip install pyyaml six

# 4단계: 버전 확인
import numpy as np
print(f"📊 numpy 버전: {np.__version__}")

try:
    import essentia
    print(f"✅ Essentia 버전: {essentia.__version__}")
except:
    print("❌ Essentia 로드 실패")

print("⚠️ Runtime > Restart runtime 클릭하세요!")


# 기본 라이브러리 import
import numpy as np
import json
import librosa
import requests
from pathlib import Path
import matplotlib.pyplot as plt
from IPython.display import Audio, display
import warnings
warnings.filterwarnings('ignore')

print(f"📊 현재 numpy 버전: {np.__version__}")

# Essentia 라이브러리 import
try:
    from essentia.standard import (
        AudioLoader,
        MonoLoader,
        TensorflowPredictEffnetDiscogs,
        TensorflowPredict2D
    )
    import essentia
    print("✅ Essentia 설치 성공!")
except ImportError as e:
    print(f"❌ Essentia 설치 실패: {e}")
    print("해결 방법:")
    print("1. Runtime > Restart runtime 클릭")
    print("2. 다시 이 셀을 실행하세요")
except AttributeError as e:
    print(f"❌ Essentia numpy 호환성 오류: {e}")
    print("해결 방법:")
    print("1. Runtime > Restart runtime 클릭")
    print("2. 다시 이 셀을 실행하세요")
    print("3. 여전히 문제가 있으면 대안 방법을 사용합니다")

  Using cached numpy-1.26.4-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (61 kB)
Using cached numpy-1.26.4-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (18.3 MB)
  Attempting uninstall: numpy
    Found existing installation: numpy 1.26.4
    Uninstalling numpy-1.26.4:
      Successfully uninstalled numpy-1.26.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
thinc 8.3.6 requires numpy<3.0.0,>=2.0.0, but you have numpy 1.26.4 which is incompatible.


  Using cached essentia_tensorflow-2.1b6.dev1110-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (1.9 kB)
Using cached essentia_tensorflow-2.1b6.dev1110-cp311-cp311-manylinux_2_17_x86_64.manylinux2014_x86_64.whl (291.4 MB)
  Attempting uninstall: essentia-tensorflow
    Found existing installation: essentia-tensorflow 2.1b6.dev1110
    Uninstalling essentia-tensorflow-2.1b6.dev1110:
      Successfully uninstalled essentia-tensorflow-2.1b6.dev1110
📊 numpy 버전: 1.26.4
✅ Essentia 버전: 2.1-beta6-dev
⚠️ Runtime > Restart runtime 클릭하세요!
📊 현재 numpy 버전: 1.26.4
✅ Essentia 설치 성공!


In [ ]:
# =============================================================================
# 2. Google Drive 마운트 및 파일 설정
# =============================================================================

def mount_drive_and_setup():
    """Google Drive 마운트 및 파일 경로 설정"""

    # Google Drive 마운트
    from google.colab import drive
    drive.mount('/content/drive')
    print("✅ Google Drive 마운트 완료!")

    # 파일 경로 설정 (사용자가 업로드한 파일들)
    drive_path = "/content/drive/MyDrive/album_art_generator_project"

    # 모델 파일 경로들
    model_files = {
        "discogs_model": f"{drive_path}/discogs-effnet-bs64-1.pb",
        "mood_model": f"{drive_path}/mtg_jamendo_moodtheme-discogs-effnet-1.pb",
        "discogs_json": f"{drive_path}/discogs-effnet-bs64-1.json",
        "mood_json": f"{drive_path}/mtg_jamendo_moodtheme-discogs-effnet-1.json"
    }

    # 테스트 음원 파일 경로 (예시)
    test_audio = f"{drive_path}/musics/Debussy_-_Arabesque_-_Aufklarung.mp3"  # 실제 파일명으로 변경하세요

    # 파일 존재 확인
    print("\n📁 파일 존재 확인:")
    for name, path in model_files.items():
        if Path(path).exists():
            print(f"✅ {name}: 존재함")
        else:
            print(f"❌ {name}: 없음 - {path}")

    if Path(test_audio).exists():
        print(f"✅ 테스트 음원: 존재함")
    else:
        print(f"❌ 테스트 음원: 없음 - {test_audio}")
        print("   실제 음원 파일명으로 수정하거나 업로드하세요")

    return model_files, test_audio

# Google Drive 마운트 및 설정 실행
model_files, test_audio_path = mount_drive_and_setup()

# 작업 디렉토리에 심볼링크 생성 (선택사항)
import os
try:
    if Path(model_files["discogs_model"]).exists():
        os.symlink(model_files["discogs_model"], "discogs-effnet-bs64-1.pb")
        os.symlink(model_files["mood_model"], "mtg_jamendo_moodtheme-discogs-effnet-1.pb")
        os.symlink(model_files["discogs_json"], "discogs-effnet-bs64-1.json")
        os.symlink(model_files["mood_json"], "mtg_jamendo_moodtheme-discogs-effnet-1.json")
        print("✅ 심볼링크 생성 완료")
except FileExistsError:
    print("✅ 심볼링크 이미 존재함")
except Exception as e:
    print(f"⚠️ 심볼링크 생성 실패: {e} (계속 진행)")

Mounted at /content/drive
✅ Google Drive 마운트 완료!

📁 파일 존재 확인:
✅ discogs_model: 존재함
✅ mood_model: 존재함
✅ discogs_json: 존재함
✅ mood_json: 존재함
❌ 테스트 음원: 없음 - /content/drive/MyDrive/album_art_generator_project/musics/Debussy_-_Arabesque_-_Aufklarung.mp3
   실제 음원 파일명으로 수정하거나 업로드하세요
✅ 심볼링크 생성 완료


In [ ]:
# =============================================================================
# 3. Colab용 음악 분류기 클래스
# =============================================================================

class ColabMusicClassifier:
    """Google Colab용 음악 분류기 - Essentia 네이티브 사용"""

    def __init__(self):
        """분류기 초기화"""

        # 메타데이터 로드
        self.genre_classes = []
        self.mood_classes = []
        self._load_metadata()

        # Essentia 모델 초기화
        self._initialize_essentia_models()

        # 분위기 태그 카테고리화
        self._categorize_mood_tags()

    def _load_metadata(self):
        """JSON 메타데이터 로드"""
        try:
            # 장르 메타데이터
            with open("discogs-effnet-bs64-1.json", 'r') as f:
                genre_metadata = json.load(f)
                self.genre_classes = genre_metadata.get('classes', [])
                print(f"✅ 장르 클래스 {len(self.genre_classes)}개 로드 완료")

            # 분위기 메타데이터
            with open("mtg_jamendo_moodtheme-discogs-effnet-1.json", 'r') as f:
                mood_metadata = json.load(f)
                self.mood_classes = mood_metadata.get('classes', [])
                print(f"✅ 분위기 클래스 {len(self.mood_classes)}개 로드 완료")

        except Exception as e:
            print(f"❌ 메타데이터 로드 실패: {e}")

    def _initialize_essentia_models(self):
        """Essentia 모델 초기화"""
        try:
            # 임베딩 추출 모델
            self.embeddings_model = TensorflowPredictEffnetDiscogs(
                graphFilename="discogs-effnet-bs64-1.pb",
                output="PartitionedCall:1"  # 임베딩 출력
            )
            print("✅ Discogs EfficientNet 모델 로드 완료")

            # 분위기 분류 모델
            self.mood_model = TensorflowPredict2D(
                graphFilename="mtg_jamendo_moodtheme-discogs-effnet-1.pb",
                output="model/Sigmoid"
            )
            print("✅ MTG Jamendo 분위기 모델 로드 완료")

            # 장르 분류용 모델 (예측 출력)
            self.genre_model = TensorflowPredictEffnetDiscogs(
                graphFilename="discogs-effnet-bs64-1.pb",
                output="PartitionedCall:0"  # 장르 예측 출력
            )
            print("✅ 장르 분류 모델 로드 완료")

        except Exception as e:
            print(f"❌ Essentia 모델 초기화 실패: {e}")

    def _categorize_mood_tags(self):
        """분위기 태그를 카테고리별로 분류"""

        # 분위기 관련 키워드들
        mood_keywords = {
            'calm', 'cool', 'dark', 'deep', 'dramatic', 'emotional', 'energetic',
            'epic', 'fast', 'fun', 'funny', 'groovy', 'happy', 'heavy', 'hopeful',
            'inspiring', 'meditative', 'melancholic', 'motivational', 'positive',
            'powerful', 'relaxing', 'romantic', 'sad', 'sexy', 'slow', 'soft',
            'upbeat', 'uplifting'
        }

        # 테마 관련 키워드들
        theme_keywords = {
            'action', 'adventure', 'ballad', 'children', 'christmas', 'dream',
            'film', 'game', 'holiday', 'love', 'movie', 'nature', 'party',
            'retro', 'space', 'sport', 'summer', 'travel'
        }

        # 기능 관련 키워드들
        function_keywords = {
            'advertising', 'background', 'commercial', 'corporate', 'documentary',
            'drama', 'soundscape', 'trailer'
        }

        # 카테고리별로 분류
        self.mood_tags = [tag for tag in self.mood_classes if tag in mood_keywords]
        self.theme_tags = [tag for tag in self.mood_classes if tag in theme_keywords]
        self.function_tags = [tag for tag in self.mood_classes if tag in function_keywords]

        print(f"📊 분위기 태그 카테고리화 완료:")
        print(f"   • 분위기: {len(self.mood_tags)}개")
        print(f"   • 테마: {len(self.theme_tags)}개")
        print(f"   • 기능: {len(self.function_tags)}개")

    def get_mood_activations_dict(self, audio):
        """
        참고 코드와 동일한 방식으로 분위기 활성화 계산 (numpy 호환성 수정)
        """
        try:
            # numpy 배열을 essentia 배열로 변환
            if isinstance(audio, np.ndarray):
                audio_essentia = essentia.array(audio.astype(np.float32))
            else:
                audio_essentia = audio

            print(f"🔍 분위기 분석 - 오디오 타입: {type(audio_essentia)}")

            # Essentia로 임베딩 추출
            embeddings = self.embeddings_model(audio_essentia)
            print(f"🔍 임베딩 추출 완료: {type(embeddings)}")

            # 분위기 분류
            activations = self.mood_model(embeddings)
            print(f"🔍 분위기 예측 완료: {type(activations)}")

            # 패치별 예측을 평균내기 (참고 코드 방식)
            activation_avs = []
            for i in range(len(activations[0])):
                vals = [activations[j][i] for j in range(len(activations))]
                activation_avs.append(sum(vals) / len(vals))

            # 딕셔너리로 변환
            activations_dict = {}
            for ind, tag in enumerate(self.mood_classes):
                if ind < len(activation_avs):
                    activations_dict[tag] = activation_avs[ind]
                else:
                    activations_dict[tag] = 0.0

            return activations_dict

        except Exception as e:
            print(f"❌ 분위기 활성화 계산 실패: {e}")
            print(f"   오디오 타입: {type(audio)}")
            if hasattr(audio, 'shape'):
                print(f"   오디오 형태: {audio.shape}")
            return {}

    def get_genre_predictions(self, audio):
        """장르 예측 (numpy 호환성 수정)"""
        try:
            # numpy 배열을 essentia 배열로 변환
            if isinstance(audio, np.ndarray):
                audio_essentia = essentia.array(audio.astype(np.float32))
            else:
                audio_essentia = audio

            print(f"🔍 오디오 타입: {type(audio_essentia)}, 형태: {audio_essentia.shape}")

            # Essentia로 장르 예측
            predictions = self.genre_model(audio_essentia)

            print(f"🔍 예측 결과 타입: {type(predictions)}")

            # 패치별 예측을 평균내기
            if len(predictions) > 1:
                prediction_avs = []
                for i in range(len(predictions[0])):
                    vals = [predictions[j][i] for j in range(len(predictions))]
                    prediction_avs.append(sum(vals) / len(vals))
            else:
                prediction_avs = predictions[0]

            # 상위 10개 장르 추출
            top_indices = np.argsort(prediction_avs)[-10:][::-1]

            genre_results = []
            for idx in top_indices:
                if idx < len(self.genre_classes):
                    genre_results.append({
                        'genre': self.genre_classes[idx],
                        'score': float(prediction_avs[idx]),
                        'index': int(idx)
                    })

            return genre_results

        except Exception as e:
            print(f"❌ 장르 예측 실패: {e}")
            print(f"   오디오 타입: {type(audio)}")
            if hasattr(audio, 'shape'):
                print(f"   오디오 형태: {audio.shape}")
            if hasattr(audio, 'dtype'):
                print(f"   오디오 dtype: {audio.dtype}")
            return []

    def get_moods(self, audio):
        """
        참고 코드와 동일한 방식으로 분위기 추출
        """
        # 분위기 활성화 계산
        mood_activations_dict = self.get_mood_activations_dict(essentia.array(audio))

        # IQR 기반 임계값 계산 (참고 코드 방식)
        values = list(mood_activations_dict.values())
        q1 = np.quantile(values, 0.25)
        q3 = np.quantile(values, 0.75)
        outlier_threshold = q3 + (1.5 * (q3 - q1))

        # 임계값 이상의 태그 선택 (melodic 제외)
        prominent_tags = [
            tag for tag, score in mood_activations_dict.items()
            if (score >= outlier_threshold) and (tag != 'melodic')
        ]

        # 카테고리별 분류
        moods = [tag for tag in prominent_tags if tag in self.mood_tags]
        themes = [tag for tag in prominent_tags if tag in self.theme_tags]
        functions = [tag for tag in prominent_tags if tag in self.function_tags]

        return moods, themes, functions, mood_activations_dict, outlier_threshold

    def classify_music(self, audio_file):
        """음악 파일 종합 분류 (numpy 호환성 개선)"""
        print(f"🎵 음악 분석 시작: {audio_file}")
        print("=" * 60)

        try:
            # 오디오 로드 (Essentia 방식)
            print("🔄 오디오 로드 중...")
            if isinstance(audio_file, str):
                # 파일 경로인 경우
                audio = MonoLoader(filename=audio_file, sampleRate=16000)()
            else:
                # 이미 로드된 오디오인 경우
                audio = audio_file

            print(f"✅ 오디오 로드 완료: {len(audio)/16000:.1f}초")
            print(f"🔍 오디오 정보: 타입={type(audio)}, 형태={audio.shape}, dtype={audio.dtype}")

            # numpy 배열로 확실히 변환 및 타입 체크
            if not isinstance(audio, np.ndarray):
                audio = np.array(audio, dtype=np.float32)
            else:
                audio = audio.astype(np.float32)

            # 메모리 레이아웃 확인 및 수정
            if not audio.flags['C_CONTIGUOUS']:
                audio = np.ascontiguousarray(audio)

            print(f"🔍 전처리 후 오디오: 타입={type(audio)}, 형태={audio.shape}, dtype={audio.dtype}")

            # 장르 분류
            print("🔄 장르 분류 중...")
            genre_results = self.get_genre_predictions(audio)
            print(f"✅ 장르 분류 완료: 상위 {len(genre_results)}개")

            # 분위기 분류
            print("🔄 분위기 분석 중...")
            moods, themes, functions, all_activations, threshold = self.get_moods(audio)
            print(f"✅ 분위기 분석 완료")

            # 상위 분위기/테마 (전체)
            top_moods = sorted(all_activations.items(), key=lambda x: x[1], reverse=True)[:10]

            # 결과 정리
            result = {
                "audio_duration": len(audio) / 16000,
                "genres": {
                    "top_genres": genre_results[:5],
                    "all_genres": genre_results
                },
                "moods": {
                    "prominent_moods": moods,
                    "prominent_themes": themes,
                    "prominent_functions": functions,
                    "top_all": top_moods,
                    "threshold": threshold
                },
                "all_activations": all_activations,
                "model_info": {
                    "using_essentia": True,
                    "genre_classes": len(self.genre_classes),
                    "mood_classes": len(self.mood_classes)
                }
            }

            return result

        except Exception as e:
            print(f"❌ 전체 분석 실패: {e}")
            return {"error": f"분석 실패: {e}"}


In [ ]:
# =============================================================================
# 4. 결과 출력 함수
# =============================================================================

def print_results(result):
    """분류 결과를 보기 좋게 출력"""

    if "error" in result:
        print(f"❌ 오류: {result['error']}")
        return

    print("\n" + "="*60)
    print("🎵 음악 분류 결과 (Essentia 네이티브)")
    print("="*60)

    print(f"⏱️  길이: {result['audio_duration']:.1f}초")

    print(f"\n🎼 상위 장르:")
    for i, genre_info in enumerate(result['genres']['top_genres'], 1):
        print(f"  {i}. {genre_info['genre']}: {genre_info['score']:.4f}")

    print(f"\n🎭 주요 분위기 (임계값: {result['moods']['threshold']:.4f}):")
    if result['moods']['prominent_moods']:
        for mood in result['moods']['prominent_moods']:
            score = result['all_activations'][mood]
            print(f"  • {mood}: {score:.4f}")
    else:
        print("  (임계값을 넘는 분위기 없음)")

    print(f"\n🎨 주요 테마:")
    if result['moods']['prominent_themes']:
        for theme in result['moods']['prominent_themes']:
            score = result['all_activations'][theme]
            print(f"  • {theme}: {score:.4f}")
    else:
        print("  (임계값을 넘는 테마 없음)")

    print(f"\n⚙️  주요 기능:")
    if result['moods']['prominent_functions']:
        for function in result['moods']['prominent_functions']:
            score = result['all_activations'][function]
            print(f"  • {function}: {score:.4f}")
    else:
        print("  (임계값을 넘는 기능 없음)")

    print(f"\n📊 상위 분위기/테마 (전체):")
    for i, (mood, score) in enumerate(result['moods']['top_all'], 1):
        print(f"  {i}. {mood}: {score:.4f}")

    print(f"\n🤖 모델 정보:")
    print(f"  • Essentia 네이티브 사용: {result['model_info']['using_essentia']}")
    print(f"  • 장르 클래스: {result['model_info']['genre_classes']}개")
    print(f"  • 분위기 클래스: {result['model_info']['mood_classes']}개")


In [ ]:
# =============================================================================
# 5. 분류기 초기화
# =============================================================================

# 분류기 생성
print("🔧 음악 분류기 초기화 중...")
classifier = ColabMusicClassifier()
print("✅ 초기화 완료!")

🔧 음악 분류기 초기화 중...
✅ 장르 클래스 400개 로드 완료
✅ 분위기 클래스 56개 로드 완료
✅ Discogs EfficientNet 모델 로드 완료
✅ MTG Jamendo 분위기 모델 로드 완료
✅ 장르 분류 모델 로드 완료
📊 분위기 태그 카테고리화 완료:
   • 분위기: 29개
   • 테마: 18개
   • 기능: 8개
✅ 초기화 완료!


In [ ]:
# =============================================================================
# 6. 간단한 테스트 함수
# =============================================================================

def test_single_audio(audio_path=None):
    """Google Drive의 단일 음원으로 테스트"""

    if audio_path is None:
        audio_path = test_audio_path

    print(f"🎵 테스트 음원: {audio_path}")

    # 파일 존재 확인
    if not Path(audio_path).exists():
        print(f"❌ 파일을 찾을 수 없습니다: {audio_path}")
        print("\n📋 해결 방법:")
        print("1. Google Drive에 음원 파일을 업로드하세요")
        print("2. 아래 코드로 정확한 파일 경로를 확인하세요:")
        print("   !ls /content/drive/MyDrive/*.mp3")
        print("3. 파일 경로를 수정하여 다시 실행하세요:")
        print("   test_single_audio('/content/drive/MyDrive/your_music.mp3')")
        return None

    # 오디오 미리듣기
    print("\n🔊 오디오 미리듣기:")
    display(Audio(audio_path))

    # 분류 실행 (Essentia 또는 하이브리드)
    try:
        print("\n🔄 Essentia 분류기로 분석 중...")
        result = classifier.classify_music(audio_path)
        print_results(result)
        return result
    except:
        print("⚠️ Essentia 분류기 실패, 하이브리드 방식 시도...")
        try:
            hybrid_classifier = HybridMusicClassifier()
            result = hybrid_classifier.classify_music(audio_path)
            print_results(result)
            return result
        except Exception as e:
            print(f"❌ 분류 실패: {e}")
            return None

In [ ]:
# =============================================================================
# 7. Drive 파일 탐색 도우미
# =============================================================================

def list_drive_files():
    """Google Drive의 파일들 확인"""
    print("📁 Google Drive 파일 목록:")

    try:
        # 음성 파일 찾기
        print("\n🎵 음성 파일들:")
        !ls -la /content/drive/MyDrive/album_art_generator_project/musics/*.mp3 2>/dev/null || echo "mp3 파일 없음"
        !ls -la /content/drive/MyDrive/album_art_generator_project/musics/*.wav 2>/dev/null || echo "wav 파일 없음"
        !ls -la /content/drive/MyDrive/album_art_generator_project/musics/*.m4a 2>/dev/null || echo "m4a 파일 없음"

        # 모델 파일 찾기
        print("\n🤖 모델 파일들:")
        !ls -la /content/drive/MyDrive/album_art_generator_project/*.pb 2>/dev/null || echo "pb 파일 없음"
        !ls -la /content/drive/MyDrive/album_art_generator_project/*.json 2>/dev/null || echo "json 파일 없음"

    except:
        print("❌ 파일 목록 확인 실패")

# 파일 목록 확인
print("\n📋 Drive 파일 확인:")
list_drive_files()


📋 Drive 파일 확인:
📁 Google Drive 파일 목록:

🎵 음성 파일들:
-rw------- 1 root root 3323687 Jun 16 07:52 /content/drive/MyDrive/album_art_generator_project/musics/Anitek_-_Tab_+_Anitek_-_Bleach.mp3
-rw------- 1 root root 4989440 Jun 16 03:29 /content/drive/MyDrive/album_art_generator_project/musics/Blood_-_All_My_Friends_Hate_Me.mp3
-rw------- 1 root root 4917691 Jun 16 07:04 /content/drive/MyDrive/album_art_generator_project/musics/Debussy_-_Arabesque_-_Aufklarung.mp3
-rw------- 1 root root 7465773 Jun 16 07:50 /content/drive/MyDrive/album_art_generator_project/musics/One_Last_Time_-_Final_Round.mp3
-rw------- 1 root root 8078264 Jun 16 03:24 /content/drive/MyDrive/album_art_generator_project/musics/Pierce_Murphy_-_A_Serpent_I_Did_Hear.mp3
-rw------- 1 root root 4880098 Jun 16 03:30 /content/drive/MyDrive/album_art_generator_project/musics/You_and_Me_-_JEKK.mp3
wav 파일 없음
m4a 파일 없음

🤖 모델 파일들:
-rw------- 1 root root 18366619 Jun 13 08:41 /content/drive/MyDrive/album_art_generator_project/discogs-ef

In [ ]:
# =============================================================================
# 8. 실행 가이드
# =============================================================================

print("\n" + "="*60)
print("🚀 테스트 실행 방법")
print("="*60)

print("1. 📁 파일 준비:")
print("   - Google Drive에 다음 파일들을 업로드하세요:")
print("   - discogs-effnet-bs64-1.pb")
print("   - mtg_jamendo_moodtheme-discogs-effnet-1.pb")
print("   - discogs-effnet-bs64-1.json")
print("   - mtg_jamendo_moodtheme-discogs-effnet-1.json")
print("   - 테스트할 음악 파일 (mp3, wav 등)")

# print("\n2. 🔄 테스트 실행:")
# print("   # 기본 테스트 (test_music.mp3)")
# print("   result = test_single_audio()")
# print()
# print("   # 특정 파일 테스트")
# print("   result = test_single_audio('/content/drive/MyDrive/your_music.mp3')")

print("\n3. 📋 파일 확인:")
print("   list_drive_files()  # Drive 파일 목록 보기")

print("\n4. 🎯 예시 실행:")
print("   # result = test_single_audio('/content/drive/MyDrive/classical_music.mp3')")

# 테스트 실행 (주석 해제하여 사용)
# result = test_single_audio()

# 업로드 및 분류 함수 실행 (주석 해제하여 사용)
result = upload_and_classify()


🚀 테스트 실행 방법
1. 📁 파일 준비:
   - Google Drive에 다음 파일들을 업로드하세요:
   - discogs-effnet-bs64-1.pb
   - mtg_jamendo_moodtheme-discogs-effnet-1.pb
   - discogs-effnet-bs64-1.json
   - mtg_jamendo_moodtheme-discogs-effnet-1.json
   - 테스트할 음악 파일 (mp3, wav 등)

2. 🔄 테스트 실행:
   # 기본 테스트 (test_music.mp3)
   result = test_single_audio()

   # 특정 파일 테스트
   result = test_single_audio('/content/drive/MyDrive/album_art_generator_project/musics/Debussy_-_Arabesque_-_Aufklarung.mp3')

3. 📋 파일 확인:
   list_drive_files()  # Drive 파일 목록 보기

4. 🎯 예시 실행:
   # 실제 파일명으로 변경하여 실행하세요
   # result = test_single_audio('/content/drive/MyDrive/album_art_generator_project/musics/Pierce_Murphy_-_A_Serpent_I_Did_Hear.mp3')
🎵 테스트 음원: /content/drive/MyDrive/album_art_generator_project/musics/Debussy_-_Arabesque_-_Aufklarung.mp3

🔊 오디오 미리듣기:



🔄 Essentia 분류기로 분석 중...
🎵 음악 분석 시작: /content/drive/MyDrive/album_art_generator_project/musics/Debussy_-_Arabesque_-_Aufklarung.mp3
🔄 오디오 로드 중...
✅ 오디오 로드 완료: 211.2초
🔍 오디오 정보: 타입=<class 'numpy.ndarray'>, 형태=(3379145,), dtype=float32
🔍 전처리 후 오디오: 타입=<class 'numpy.ndarray'>, 형태=(3379145,), dtype=float32
🔄 장르 분류 중...
🔍 오디오 타입: <class 'numpy.ndarray'>, 형태: (3379145,)
🔍 예측 결과 타입: <class 'numpy.ndarray'>
✅ 장르 분류 완료: 상위 10개
🔄 분위기 분석 중...
🔍 분위기 분석 - 오디오 타입: <class 'numpy.ndarray'>
🔍 임베딩 추출 완료: <class 'numpy.ndarray'>
🔍 분위기 예측 완료: <class 'numpy.ndarray'>
✅ 분위기 분석 완료

🎵 음악 분류 결과 (Essentia 네이티브)
⏱️  길이: 211.2초

🎼 상위 장르:
  1. Classical---Contemporary: 0.2494
  2. Electronic---New Age: 0.1304
  3. Classical---Neo-Classical: 0.1208
  4. Electronic---Ambient: 0.0937
  5. Classical---Post-Modern: 0.0676

🎭 주요 분위기 (임계값: 0.0651):
  • emotional: 0.0723
  • inspiring: 0.1232
  • meditative: 0.0969
  • relaxing: 0.2660
  • romantic: 0.0747
  • sad: 0.0772

🎨 주요 테마:
  (임계값을 넘는 테마 없음)

⚙️  주요 기능:
  • backgro